In [1]:
import json
import pandas as pd
import numpy as np
import a1chemy as a1
import a1chemy.indicators as indicators
import a1chemy.data_source as data_source
from tqdm.notebook import tqdm
import random
import time
import pymongo

mongo_client = pymongo.MongoClient("mongodb://localhost:27017/", username='a1chemy', password='1B2C9046-E3CC-447F-9961-E125759BA44F')
mongo_ticks_client = data_source.MongoTicks(mongo_client)

# sectors data
sectors_list = a1.read_json_from_file('/Users/line/workspace/freedom/A1chemy/data/sw_sector.json')
stock_sector_map = {}
sectors = set()
for stock in sectors_list:
    sector = stock['sector']
    stock_sector_map[stock['symbol']] = sector
    sectors.add(sector)

# stocks
stocks = a1.read_json_from_file('/Users/line/workspace/freedom/A1chemy/data/csi_300.json')
sci_300_sector_map = {}
for stock in stocks:
    sector = stock_sector_map[stock['symbol']]
    sector_list = sci_300_sector_map.setdefault(sector, [])
    sector_list.append(stock)

sci_300_sector_count_map = {}
for k, v in sci_300_sector_map.items():
    sci_300_sector_count_map[k] = len(v)

for k, v in sci_300_sector_count_map.items():
    company_name_list = ",".join([d['name'] for d in sci_300_sector_map[k]])
    print(k + "," + str(v) + ",   " + company_name_list)


    

银行,27,   浦发银行,华夏银行,民生银行,招商银行,江苏银行,杭州银行,西安银行,南京银行,渝农商行,兴业银行,北京银行,上海银行,农业银行,交通银行,工商银行,长沙银行,邮储银行,光大银行,成都银行,浙商银行,建设银行,中国银行,贵阳银行,中信银行,平安银行,宁波银行,青农商行
交通运输,17,   白云机场,上海机场,上港集团,南方航空,东方航空,海航控股,圆通速递,大秦铁路,宁波港,春秋航空,中国国航,青岛港,京沪高铁,中远海控,韵达股份,顺丰控股,申通快递
钢铁,4,   包钢股份,宝钢股份,中信特钢,河钢股份
公用事业,9,   华能国际,华能水电,华电国际,川投能源,国电电力,国投电力,长江电力,中国核电,中国广核
化工,10,   中国石化,中国巨石,安迪苏,万华化学,恒力石化,浙江龙盛,君正集团,恒逸石化,荣盛石化,龙蟒佰利
非银金融,37,   中信证券,国投资本,国金证券,西南证券,五矿资本,中航资本,海通证券,东方证券,招商证券,中信建投,财通证券,天风证券,东兴证券,国泰君安,红塔证券,中国平安,中国人保,新华保险,兴业证券,东吴证券,中国太保,中国人寿,华泰证券,光大证券,浙商证券,中国银河,方正证券,申万宏源,天茂集团,国元证券,广发证券,长江证券,西部证券,国信证券,长城证券,华林证券,东方财富
机械设备,5,   三一重工,恒立液压,中国中车,中联重科,徐工机械
国防军工,10,   中直股份,中国卫星,中航电子,中国动力,中航沈飞,航发动力,中国卫通,中国重工,中航飞机,中航光电
房地产,15,   保利地产,雅戈尔,新湖中宝,华夏幸福,金地集团,绿地控股,上海临港,新城控股,万科A,华侨城A,金科股份,阳光城,中南建设,招商蛇口,荣盛发展
通信,6,   中国联通,亨通光电,烽火通信,中天科技,中兴通讯,亿联网络
汽车,10,   宇通客车,上汽集团,广汇汽车,福耀玻璃,华域汽车,广汽集团,长城汽车,潍柴动力,长安汽车,比亚迪
建筑装饰,9,   葛洲坝,上海建工,中国化学,中国铁建,中国中铁,中国中冶,中国建筑,中国电建,中国交建
医药生物,25,   同仁堂,复星医药,恒瑞医药,白云山,片仔癀,通化东宝,九州通,上海医药,药明康德,安图生物,云南白药,长春高新,华东医药,新和成,华兰生物,美年健康,上海莱士,科伦药业,康

In [2]:
from a1chemy.common.ticks import Ticks
stock_candle_data_map = {}
stock_symbol_list = [stock['symbol'] for stock in stocks]
print(len(stock_symbol_list))
for tick in mongo_ticks_client.find({'symbol':{'$in': stock_symbol_list}}):   
    tick.raw_data['MA20'] = indicators.sma(data=tick.close(), day=20)
    tick.convert_tz(tz='Asia/Shanghai')
    stock_candle_data_map[tick.symbol] = tick
print(len(stock_candle_data_map))

300
300


In [3]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

breath_color_list = [
    '#FF0000',
    '#FF3333',
    '#FF6666',
    '#FF9999',
    '#FFCCCC',
    '#CCFFCC',
    '#99FF99',
    '#66FF66',
    '#33FF33',
    '#00CC00'
]

def market_breath_color(v):
    '''
    highlight the maximum in a Series yellow.
    '''
    color_index = 0 if float(v) <= 0 else int(float(v)/10-1)
    return 'background-color: ' + breath_color_list[color_index]


start_time = pd.Timestamp("2020-05-01 00:00:01", tz="Asia/Shanghai")
market_breath = {}
last_day_active_stocks = {}
for k, v in stock_candle_data_map.items():
    for i in range(0, len(v.index())):
        close = v.close()[i]
        ma20 = v.raw_data['MA20'][i]
        current_day = v.index()[i]
        sector = stock_sector_map[k]
        current_day_data = market_breath.setdefault(str(current_day), {})

        value = current_day_data.setdefault(sector, {})
        all_value = current_day_data.setdefault('all', {})
        above = value.setdefault('above', 0)
        stocks_count = value.setdefault('all', 0)
        
        all_above = all_value.setdefault('above', 0)
        all_stocks_count = all_value.setdefault('all', 0)
        if close > ma20:
            if i == (len(v.index()) -1):
                last_day_sector_active_stock_list = last_day_active_stocks.setdefault(sector, [])
                last_day_sector_active_stock_list.append(v.name)
            current_day_data[sector]['above'] = above + 1
            current_day_data['all']['above'] = all_above + 1
        value['all'] = stocks_count + 1
        all_value['all'] = all_stocks_count + 1

for k, v in last_day_active_stocks.items():
    print("{}: {}".format(k, ",".join(v)))
        
for k, v in market_breath.items():
    for name, value in v.items():
        value['percent'] = round(float(value['above'])*100/float(value['all']),2)

market_breath_show_data = []
for k, v in sorted(list(market_breath.items()), key=lambda x:x[0].lower(), reverse=True):
    result = [k[0:10]]
    for sector in sectors:
        result.append(str(v.get(sector, {}).get('percent', 0)))
    result.append(str(v.get('all',{}).get('percent', 0)))
    market_breath_show_data.append(result)
market_breath_column_name_list = ['日期']
market_breath_column_name_list.extend(sectors)
market_breath_column_name_list.append("ALL")
market_breath_data_frame=pd.DataFrame(market_breath_show_data, columns=market_breath_column_name_list)

market_breath_data_frame.style.applymap(market_breath_color, subset=market_breath_column_name_list[1:])

有色金属: 天齐锂业,紫金矿业,中国铝业,南山铝业,白银有色,江西铜业,赣锋锂业,洛阳钼业,中金黄金,华友钴业,北方稀土,合盛硅业,方大炭素
汽车: 广汽集团,比亚迪,长城汽车,上汽集团,宇通客车,华域汽车,福耀玻璃,长安汽车,潍柴动力
交通运输: 中远海控,上港集团,宁波港,中国国航,青岛港,春秋航空,东方航空,大秦铁路,海航控股,南方航空,上海机场,京沪高铁,白云机场
采掘: 美锦能源,宝丰能源,中海油服,陕西煤业,兖州煤业,海油工程,中煤能源,中国神华,海油发展,中国石油
化工: 安迪苏,恒力石化,万华化学,中国巨石,恒逸石化,浙江龙盛,龙蟒佰利,荣盛石化,中国石化
国防军工: 中航飞机,中航电子,航发动力,中直股份,中航光电,中航沈飞,中国动力,中国卫星,中国重工,中国卫通
电子: 亿纬锂能,三环集团,大族激光,三安光电,京东方A,TCL科技,工业富联,沪电股份,海康威视,闻泰科技,视源股份,兆易创新,生益科技
机械设备: 三一重工,恒立液压,中联重科,中国中车
食品饮料: 山西汾酒,今世缘,顺鑫农业,五粮液,泸州老窖,养元饮品,洋河股份,贵州茅台,双汇发展
钢铁: 宝钢股份,中信特钢,河钢股份,包钢股份
电气设备: 通威股份,国电南瑞,特变电工,上海电气,金风科技,汇川技术,正泰电器
传媒: 分众传媒,东方明珠,中国电影,万达电影
建筑材料: 北新建材,东方雨虹,金隅集团,海螺水泥
计算机: 中科曙光,用友网络,科大讯飞,同花顺
医药生物: 新和成,白云山,九州通,上海医药,华东医药
家用电器: 苏泊尔,海尔智家,三花智控,老板电器,格力电器,美的集团
公用事业: 华能水电,川投能源,国电电力,华能国际,华电国际,国投电力,中国核电
轻工制造: 欧派家居
通信: 亿联网络,亨通光电,中天科技,烽火通信,中兴通讯
非银金融: 光大证券,中信建投,华林证券,国金证券,中信证券,申万宏源,东兴证券,长城证券,天风证券,西南证券,浙商证券,国元证券,广发证券,五矿资本,东吴证券,东方财富,中国银河,国投资本,东方证券,招商证券,中国平安,中国太保,长江证券,兴业证券,中航资本
纺织服装: 海澜之家
建筑装饰: 中国化学,中国建筑,中国中冶,中国中铁,上海建工,中国铁建,中国电建,中国交建
房地产: 新湖中宝,万科A,雅戈尔,保利地产,荣盛发展,华侨城A,华夏幸福,